In [1]:
from dotenv import load_dotenv
import os
load_dotenv()

True

In [2]:
api_key = os.environ.get('GOOGLE_API_KEY')

In [3]:
if not api_key:
    raise ValueError('GOOGLE_API_KEY environment variable not found')
print("api_key loaded successfully")

api_key loaded successfully


In [4]:
from llama_index.readers.web import SimpleWebPageReader
from llama_index.core import VectorStoreIndex
from llama_index.embeddings.gemini import GeminiEmbedding
from llama_index.core import StorageContext
from llama_index.core import load_index_from_storage
import google.generativeai as genai
from llama_index.llms.gemini import Gemini
from IPython.display import Markdown
from IPython.display import display

In [5]:
genai.configure(api_key=api_key)

In [6]:
for models in genai.list_models():
    print(models.name)

models/chat-bison-001
models/text-bison-001
models/embedding-gecko-001
models/gemini-1.0-pro-latest
models/gemini-1.0-pro
models/gemini-pro
models/gemini-1.0-pro-001
models/gemini-1.0-pro-vision-latest
models/gemini-pro-vision
models/gemini-1.5-pro-latest
models/gemini-1.5-pro-001
models/gemini-1.5-pro-002
models/gemini-1.5-pro
models/gemini-1.5-pro-exp-0801
models/gemini-1.5-pro-exp-0827
models/gemini-1.5-flash-latest
models/gemini-1.5-flash-001
models/gemini-1.5-flash-001-tuning
models/gemini-1.5-flash
models/gemini-1.5-flash-exp-0827
models/gemini-1.5-flash-002
models/gemini-1.5-flash-8b
models/gemini-1.5-flash-8b-001
models/gemini-1.5-flash-8b-latest
models/gemini-1.5-flash-8b-exp-0827
models/gemini-1.5-flash-8b-exp-0924
models/gemini-2.0-flash-exp
models/gemini-exp-1206
models/gemini-exp-1121
models/gemini-exp-1114
models/gemini-2.0-flash-thinking-exp-01-21
models/gemini-2.0-flash-thinking-exp
models/gemini-2.0-flash-thinking-exp-1219
models/learnlm-1.5-pro-experimental
models/emb

In [7]:
for models in genai.list_models():
    if 'generateContent' in models.supported_generation_methods:
        print(models.name)

models/gemini-1.0-pro-latest
models/gemini-1.0-pro
models/gemini-pro
models/gemini-1.0-pro-001
models/gemini-1.0-pro-vision-latest
models/gemini-pro-vision
models/gemini-1.5-pro-latest
models/gemini-1.5-pro-001
models/gemini-1.5-pro-002
models/gemini-1.5-pro
models/gemini-1.5-pro-exp-0801
models/gemini-1.5-pro-exp-0827
models/gemini-1.5-flash-latest
models/gemini-1.5-flash-001
models/gemini-1.5-flash-001-tuning
models/gemini-1.5-flash
models/gemini-1.5-flash-exp-0827
models/gemini-1.5-flash-002
models/gemini-1.5-flash-8b
models/gemini-1.5-flash-8b-001
models/gemini-1.5-flash-8b-latest
models/gemini-1.5-flash-8b-exp-0827
models/gemini-1.5-flash-8b-exp-0924
models/gemini-2.0-flash-exp
models/gemini-exp-1206
models/gemini-exp-1121
models/gemini-exp-1114
models/gemini-2.0-flash-thinking-exp-01-21
models/gemini-2.0-flash-thinking-exp
models/gemini-2.0-flash-thinking-exp-1219
models/learnlm-1.5-pro-experimental


In [8]:
documents = SimpleWebPageReader(html_to_text=True)

In [9]:
documents

SimpleWebPageReader(is_remote=True, html_to_text=True)

In [10]:
data = documents.load_data(urls = ["https://www.javatpoint.com/machine-learning"])

In [11]:
print(data[0].text)

[![Logo](/static/img/logo.png)](/)

__

__

Tutorials

×  

### Python

[Python](/python-tutorial) [Django](/django-tutorial) [Numpy](/numpy-tutorial)
[Pandas](/python-pandas) [Tkinter](/python-tkinter) [Pytorch](/pytorch)
[Flask](/flask-tutorial) [OpenCV](/opencv)

### AI, ML and Data Science

[Artificial Intelligence](/artificial-intelligence-ai) [Machine
Learning](/machine-learning) [Data Science](/data-science) [Deep
Learning](/deep-learning) [TensorFlow](/tensorflow) [Artificial Neural
Network](/artificial-neural-network) [Matplotlib](/matplotlib) [Python
Scipy](/python-scipy)

### Java

[Java](/java-tutorial) [Servlet](/servlet-tutorial) [JSP](/jsp-tutorial)
[Spring Boot](/spring-boot-tutorial) [Spring Framework](/spring-tutorial)
[Hibernate](/hibernate-tutorial) [JavaFX](/javafx-tutorial) [Java Web
Services](/java-web-services-tutorial)

### B.Tech and MCA

[DBMS](/dbms-tutorial) [Data Structures](/data-structure-tutorial) [Operating
System](/operating-system) [Computer Network]

In [12]:
gemini_embedding = GeminiEmbedding(model_name='models/embedding-001')

In [13]:
gemini_embedding

GeminiEmbedding(model_name='models/embedding-001', embed_batch_size=10, callback_manager=<llama_index.core.callbacks.base.CallbackManager object at 0x00000198B1055D50>, num_workers=None, title=None, task_type='retrieval_document', api_key=None)

In [14]:
model = Gemini(model_name = 'models/gemini-pro',api_key=api_key)

In [15]:
from llama_index.core.node_parser import SentenceSplitter
from llama_index.core import Settings

Settings.llm = model
Settings.embed_model = gemini_embedding
Settings.node_parser = SentenceSplitter(chunk_size=512, chunk_overlap=20)
Settings.num_output = 512
Settings.context_window = 3900

In [16]:
Settings.node_parser 

SentenceSplitter(include_metadata=True, include_prev_next_rel=True, callback_manager=<llama_index.core.callbacks.base.CallbackManager object at 0x00000198B1057DF0>, id_func=<function default_id_func at 0x00000198AD4501F0>, chunk_size=512, chunk_overlap=20, separator=' ', paragraph_separator='\n\n\n', secondary_chunking_regex='[^,.;。？！]+[,.;。？！]?')

In [17]:
index = VectorStoreIndex.from_documents(data,settings = Settings)
# index.storage_context.persist()

In [18]:
query_engine = index.as_query_engine()

In [19]:
response = query_engine.query("tell me about the history of machine learning")

In [20]:
def to_markdown(text):
    return Markdown(text)

In [21]:
new_response = to_markdown(response.response)

In [22]:
new_response

The history of machine learning can be divided into several eras:

**Pre-1940:**
- 1834: Charles Babbage conceived a device that could be programmed with punch cards.
- 1936: Alan Turing gave a theory on how a machine can determine and execute a set of instructions.

**The era of stored program computers:**
- 1940: The first manually operated computer, "ENIAC" was invented, which was the first electronic general-purpose computer.
- 1943: A human neural network was modeled with an electrical circuit.
- 1949: EDSAC, a stored program computer, was invented.
- 1951: EDVAC, another stored program computer, was invented.

**Computer machinery and intelligence:**
- 1950: Alan Turing published a seminal paper, "Computer Machinery and Intelligence," on the topic of artificial intelligence.

**Machine intelligence in Games:**
- 1952: Arthur Samuel created a program that helped an IBM computer to play a checkers game.
- 1959: The term "Machine Learning" was first coined by Arthur Samuel.

**The first "AI" winter:**
- 1974-1980: This was a tough time for AI and ML researchers, and this duration was called as **AI winter**.

**Machine Learning from theory to reality:**
- 1959: The first neural network was applied to a real-world problem to remove echoes over phone lines using an adaptive filter.

In [23]:
model = genai.GenerativeModel(model_name="models/gemini-pro")

In [24]:
model.count_tokens(response.response)

total_tokens: 336